## Interactive data visualization using plotly

In [1]:
import pandas as pd
import numpy as np

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

####  Since Plotly plots are interactive, they make use of JavaScript behind the scenes, we need to connect jupyter notebook with JavaScript
#### Also, we need to import the Cufflink library and make sure that we will be using it offline. 

In [2]:
init_notebook_mode(connected=True)
import cufflinks as cf
cf.go_offline()

#### Let's import our data

In [23]:
data = pd.read_excel(r"C:\Users\maa5m\Desktop\2018_school\EN.605.662.82.SP20 Data Visualization\proj4\COVID19_geographic_disbtribution_worldwide.xlsx")

### Let's do some data cleaning

In [24]:
df = data[data.cases>=0].reset_index(drop=True)

### Plotly for Geographical Plots
#### To draw geographical plots with Plotly, we will use Choropleth Maps. Choropleth Maps are special types of Plotly plots that are used to plot geographical data.

In [5]:
import chart_studio.plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

init_notebook_mode(connected=True)
import pandas as pd

### Geographical Maps for the United States
#### Step 1: Create a Data Dictionary. This contains the data that you want to display on the map

In [6]:
map_data = dict(type='choropleth',
            locations=['MI', 'CO', 'FL', 'IN'],
            locationmode='USA-states',
            colorscale='Portland',
            text=['Michigan', 'Colorado', 'Florida', 'Indiana'],
            z=[1.0,2.0,3.0,4.0],
            colorbar=dict(title="USA States")
           )

#### Step 2: Create a Layout dictionary

In [7]:
map_layout = dict(geo = {'scope':'usa'})

#### Step 3: Create Graph Object using plotly.graph_objs class. The object takes two parameters: data and layout. We will pass our data dictionary to the first parameter and the layout dictionary to the second parameter

In [8]:
iplot(go.Figure(data=[map_data], layout=map_layout))

#### World map

In [9]:
aggregate = df.groupby('countriesAndTerritories')['cases'].sum()

In [10]:
df_max_cases = df.loc[df.groupby('countriesAndTerritories')['cases'].idxmax()].reset_index(drop=True)
#idx = df.groupby('countriesAndTerritories').apply(lambda x: x['cases'].sum())
#df.loc[idx]

In [11]:
df_max_cases.head()

dateRep  day  month  year  cases  deaths countriesAndTerritories geoId  \
0 2020-04-26   26      4  2020    112       4             Afghanistan    AF   
1 2020-04-26   26      4  2020     34       0                 Albania    AL   
2 2020-04-04    4      4  2020    185      42                 Algeria    DZ   
3 2020-03-28   28      3  2020     43       0                 Andorra    AD   
4 2020-04-19   19      4  2020      5       0                  Angola    AO   

  countryterritoryCode  popData2018 continentExp  
0                  AFG   37172386.0         Asia  
1                  ALB    2866376.0       Europe  
2                  DZA   42228429.0       Africa  
3                  AND      77006.0       Europe  
4                  AGO   30809762.0       Africa

In [12]:
#Create a Data Dictionary
map_data = dict(
        type='choropleth',
        locations=df_max_cases['countryterritoryCode'],
        z=df_max_cases['cases'],
        text=df_max_cases['countriesAndTerritories'],
        colorbar={'title': 'World Covid19 Infection'},
      )


#Create a layout Dictionary
map_layout = dict(
    title='Maximum Covid19 cases recorded in a day',
    geo=dict(showframe=True)
)

# Create Graph Object using plotly.graph_objs class
map_actual = go.Figure(data=[map_data], layout=map_layout)

#call the plotly method
iplot(map_actual)

### Using plotly express function

In [13]:
import plotly.express as px

total_cases = df_max_cases['cases'].sum()

fig = px.choropleth(df_max_cases, locations="countryterritoryCode", color="cases",
                    color_continuous_scale=px.colors.diverging.BrBG,
                    color_continuous_midpoint=total_cases,
                    title="Maximum Covid19 cases recorded in a day %.1f" % total_cases)
fig.show()

In [14]:
import plotly.express as px

fig = px.parallel_categories(df_max_cases, color="cases", color_continuous_scale=px.colors.diverging.BrBG)
fig.show()

In [15]:
df_sum = df.loc[df.groupby('countriesAndTerritories')['cases'].idxmax()].reset_index(drop=True)

### Correlation between number of cases and  deaths in a day

In [16]:
fig = px.violin(df_max_cases, y="deaths", x="cases", color="countriesAndTerritories", box=True, points="all", 
                )
fig.show()

In [17]:
df_max_cases['dateRep'] = pd.to_datetime(df_max_cases['dateRep']).astype('string')
mins = df_max_cases['cases'].min()
maxs = df_max_cases['cases'].max()
fig = px.choropleth(df_max_cases, locations="countryterritoryCode", color="cases", hover_name="countriesAndTerritories", 
                    animation_frame="dateRep", range_color=[mins,maxs])
fig.show()

In [18]:
mins = df_max_cases['cases'].min()
maxs = df_max_cases['cases'].max()

fig = px.scatter(df_max_cases, x="cases", y="deaths", size="cases", color="countriesAndTerritories",  
                range_color=[mins,maxs], hover_name="dateRep", log_x=True, size_max=40)
fig.show()

### Let's visualize how the deaths trend with time. We will calculate the cumulative sum and total sum for each country

In [19]:
def sum_data(data):
    df1 = data[['dateRep', 'popData2018', 'countryterritoryCode', 'countriesAndTerritories']]
    df1['cumsum_cases'] = data['cases'].cumsum()
    df1['cumsum_deaths'] = data['deaths'].cumsum()
    
    df2 = data[['dateRep', 'popData2018', 'countryterritoryCode', 'countriesAndTerritories']]
    df2['total_cases'] = data['cases'].sum()
    df2['total_deaths'] = data['deaths'].sum()
    
    return df1

df = df.sort_values(by = 'dateRep').reset_index(drop=False)
data = df.groupby('countriesAndTerritories').apply(sum_data)

In [20]:
mins = data['cumsum_cases'].min()
maxs = data['cumsum_cases'].max()

fig = px.scatter(data, x="cumsum_cases", y="cumsum_deaths", size="cumsum_cases", color="countriesAndTerritories",  
                range_color=[mins,maxs], hover_name="dateRep", log_x=True, size_max=40)
fig.show()

In [21]:
mins = data['cumsum_cases'].min()
maxs = data['cumsum_cases'].max()

fig = px.scatter(data, x="dateRep", y="cumsum_cases", size="cumsum_deaths", color="countriesAndTerritories",  
                range_color=[mins,maxs], hover_name="dateRep")
fig.show()